# PP-LiteSeg 道路分割模型 解读, 训练, 评估

山东大学（威海）数据科学与人工智能实验班

暑期科研实训项目第一部分

### 小组成员

- WJY, LYQ
- RPF, SCZ

2022 年 7 月 23 日

### 注意： AI Studio 的默认项目预览界面（https://aistudio.baidu.com/aistudio/projectdetail/4320864 ）可能无法正确显示图像，请 fork 项目启动环境后进入运行环境内查看此 Notebook, 部分图片需要您等待“正在同步文件”的通知消失之后，刷新页面才会显示。请等待文件同步结束之后再运行此 Notebook 中的代码块.

## 参考资料
- PaddleSeg: https://github.com/PaddlePaddle/PaddleSeg
- PP-LittleSeg: https://arxiv.org/abs/2204.02681, https://github.com/PaddlePaddle/PaddleSeg/tree/release/2.5/configs/pp_liteseg
- Cityscapes dataset, CamVid Dataset

## 模型选择

在拜读了 ViT-Adapter, PIDNet, HRNetV2+OCR+, PP-LiteSeg 等模型的论文之后, 我们最终选择了在此大作业使用 PP-LiteSeg 模型.

- ViT-Adapter: 对 Vision Transformer 的改进, Vision Transformer 将广泛应用于自然语言处理的 Transformer 模型应用到了图像处理上, 是一大创新. ViT-Adapter 模型是 2022 年才提出的一个新模型,论文见 https://arxiv.org/pdf/2205.08534v2.pdf, 它在 Cityscapes 数据集的测试集排行上现居第一. 但是网络过于复杂,无法实现实时预测,因此我们没有选择此模型.
- HRNetV2+OCR+: 该模型和 PP-LiteSeg 一样也是 PaddleSeg 下属的一个模型, 目前在 Cityscapes 数据集的测试集榜单上现居第二名, 仅次于 ViT-Adapter, 论文见 https://arxiv.org/pdf/1909.11065v6.pdf , 在 AIStudio 上亦有其他用户在 KITTI-Step 数据集上训练了此模型,参见: https://aistudio.baidu.com/aistudio/projectdetail/4038141?contributionType=1 , 我们出于和 ViT-Adapter 模型一样的理由(无法实时预测)没有选择此模型.
- PIDNet: 这也是一个 2022 年新鲜出炉的模型, arxiv 的论文上标的是 2022年 6月, 该模型的大中小模型在 Cityscapes 数据集的测试集的实时预测模型榜单上占据了第一, 第三, 第四名的位置. 它的大中小模型的 FPS 分别为 31.1, 42.2, 93.2, 可以达到我们的自动驾驶的实时性的要求, 但是我们发现它的FPS是在 Nvidia RTX 3090 高端显卡上得到的结果, 而我们的自动驾驶出于低延迟的要求需要模型运行在我们的本地, 我们估计在我们本地的中低端显卡上, 可能并不能很好的达到实时预测的目的,于是没有选择该模型, 论文参见 https://arxiv.org/pdf/2206.02066v2.pdf
- PP-LiteSeg: PP-LiteSeg-B2 在 Cityscapes 数据集的测试集的实时预测模型榜单上排名第六, 这也是一个 2022 年新提出的模型, 它虽然排名稍微靠后了一点, 但是它是在排名前十的模型中FPS最高的, FPS 为 102.6, 而且得出这个 FPS 的显卡是 Nvidia GTX 1080Ti, 这个显卡比前十名中其他模型使用的 3090, 2080Ti 等显卡相对低端一些, 我们有十足的把握该模型能够在我们本地的中低端显卡上做到实时运行,于是我们最终选择了此模型. 对该模型的更详细的解读请见下文.

## PaddleSeg 介绍

PaddleSeg 是一个易用的, 端到端的高效图像语义分割模型开发套件(https://arxiv.org/abs/2101.06175), 我们可以很方便的使用 PaddleSeg 来执行多卡分布式训练, 评估模型, 复用现有的模型等.

## PP-LiteSeg 模型讲解

此 Notebook 使用的是 PP-LiteSeg 这个模型, 原作者的论文(英文)参见: https://arxiv.org/pdf/2204.02681.pdf

### PP-LiteSeg 模型的优点

现有的许多图像语义分割模型(FCN, PSPNet, SFNet)都因为其过高的计算复杂性而无法做到实时预测, 而一些降低了计算复杂度的模型却无法很好的平衡准确度和预测速度, 比如 Espnetv2, BiSeNetV2 和 STDCSeg. 

其中 STDCSeg 提出了一种新型骨干网络: STDC, 这个网络可以很好的提升计算效率, PP-LiteSeg 所适用的骨干网络正是 STDC.

而 PP-LiteSeg 则可以很好的平衡准确度和预测速度, 这也是我们在本次大作业中选用这个模型的原因. 我们的智能小车在行驶的过程中需要实时的预测数据.

### PP-LiteSeg 模型架构






![Screenshot_16.png](work/images/Arch.png)




PP-LiteSeg 由三个模块组成,分别是 编码器(encoder), 简单金字塔池化模块(SPPM)和解码器(Decoder), 这是一个典型的 Encoder-Decoder 架构的神经网络.

其中,
- Encoder 采用的是 STDCNet, 更具体一点,此 Notebook 中使用的是 STDC2
- SPPM 是作者在论文中提出的,是对现有的 PPM 的改进
- Decoder 是作者在论文中提出的灵活轻量级解码器(FLD)




### Encoder 讲解

PP-LiteSeg 使用了来自 STDC-Seg 的 STDCNet 骨干网络作为 Encoder, 以下为 STDCNet 的 网络架构.

![](work/images/Screenshot_17.png)

网络中用到了 ConvX 模块和 STDC 模块, ConvX 就是平常的 卷积-批标准化-ReLU, 而 STDC 模块则是论文作者提出的一个新的主要由卷积构成的模块,全称为 Short-Term Dense Concatenate Module (STDCM), 这个模块的结构也展示在了上图中.

STDC 模块的感受野见下表:

| STDC module | Block1 | Block2 | Block3 | Block4 | Fusion |
| :--- | :--- | :--- | :--- | :---: | :---: |
| RF(S=1) | 1x1 | 3x3 | 5x5 | 7x7 | 1x1,3x3 5x5,7x7 |
| RF(S=2) | 1x1 | 3x3 | 7x7 | 11 x11 | 3x3, 7x7,11 x11 |


STDCNet 的 Paddle 实现可以参考: https://github.com/PaddlePaddle/PaddleSeg/blob/release/2.5/paddleseg/models/backbones/stdcnet.py



### SPPM 讲解

下图为 SPPM 的结构, Conv 表示 1x1 的将通道数减小的卷积, Resize 使用的是双线性插值(Bilinear Interpolation)进行上采样

![](work/images/Screenshot_18.png)

简单金字塔池化模块是对原先在 PSPNet 的论文中提出的金字塔池化模块(PPM)的改进. 

PPM 的架构见下图:

![](work/images/PPM.png)

PPM 的 Paddle 实现可以参考 https://github.com/PaddlePaddle/PaddleSeg/blob/2366ce423d753853f76a1f04ead4079a1e85e428/paddleseg/models/layers/pyramid_pool.py#L117 , 但是注意这里的实现与原论文稍有不同.

SPPM 的代码见 https://github.com/PaddlePaddle/PaddleSeg/blob/2366ce423d753853f76a1f04ead4079a1e85e428/paddleseg/models/pp_liteseg.py#L197, 注意代码中名称为 PPContextModule, 不是 SPPM.


SPPM 和 PPM 的主要区别在于: SPPM 减少了运算过程中和输出的通道数,且 SPPM 不将原输入加入输出中, SPPM 使用加法代替了 PPM 中的连接操作(Concatenation). 

所以 SPPM 比 PPM 更加轻量级.

### Decoder(FLD) 讲解

![](work/images/Screenshot_19.png)


与大多数语义分割模型在 Decoder 中保持通道数基本不变的做法不同, PP-LiteSeg 的 Decoder 的通道数从输入到输出是不断减小的. 如果保持通道数不变, 而 feature map 的尺寸却不断增大,就会导致越靠近输出端计算资源消耗越多. 通过从输入端到输出端逐渐减小通道数, PP-LiteSeg 降低了计算复杂性,平衡了 Decoder 中各层所占用的计算资源,而且实践表明尽管通道数减少了,这几乎没有影响到 PP-LiteSeg 的预测准确率.



#### UAFM 讲解

Unified Attention Fusion Module, 简称 UAFM, 是原作者提出的一种新的融合多个层次特征的模块.

<!-- ![](images/Screenshot_20.png) -->


在 UAFM 中, 我们使用一个注意力模块产生权重 $\alpha$ (注意此处 $\alpha$ 不是一个数值,而是一个张量),然后进行加法和乘法运算得到 $F_{out}=F_{up}\cdot\alpha + F_{low}\cdot(1-\alpha)$

其中 $F_{up}$ 是 $F_{high}$ 经过上采样得到的.

下面介绍两种注意力模块:

##### Spatial Attention Module

![](work/images/Screenshot_21.png)

假设输入为 $F_{u p} \in R^{C \times H \times W}$ 和 $F_{\text {low }} \in R^{C \times H \times W}$, 我们沿通道方向分别执行取平均和最大值操作,可以得到四个 $R^{1 \times H \times W}$ 尺寸的输出, 拔他们沿通道方向连接,得到 $R^{4 \times H \times W}$ 尺寸的输出,然后经过卷积, 得到 $R^{1 \times H \times W}$ 的输出, 最后通过 Sigmoid 激活函数得到 $\alpha$

##### Channel Attention Module

![](work/images/Screenshot_22.png)

和 Spatial Attention Module 类似, 只不过压缩空间特征而非通道, 不再赘述.


## 下载安装 PaddleSeg

In [4]:
# 下载 PaddleSeg
! GIT_SSL_NO_VERIFY=1 git clone https://hub.fastgit.xyz/PaddlePaddle/PaddleSeg --depth=1

正克隆到 'PaddleSeg'...
remote: Enumerating objects: 1601, done.
remote: Counting objects: 100% (1601/1601), done.
remote: Compressing objects: 100% (1297/1297), done.
remote: Total 1601 (delta 381), reused 976 (delta 225), pack-reused 0
接收对象中: 100% (1601/1601), 46.34 MiB | 553.00 KiB/s, 完成.
处理 delta 中: 100% (381/381), 完成.
检查连接... 完成。


In [5]:
%cd PaddleSeg
!pip install -r requirements.txt

/home/aistudio/PaddleSeg
Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple


## 验证 PaddleSeg 安装成功

In [6]:
!sh tests/run_check_install.sh

--2022-07-09 14:17:29--  https://paddleseg.bj.bcebos.com/dataset/optic_disc_seg.zip
正在解析主机 paddleseg.bj.bcebos.com (paddleseg.bj.bcebos.com)... 100.67.200.6
正在连接 paddleseg.bj.bcebos.com (paddleseg.bj.bcebos.com)|100.67.200.6|:443... 已连接。
已发出 HTTP 请求，正在等待回应... 200 OK
长度： 19300588 (18M) [application/zip]
正在保存至: “optic_disc_seg.zip”

optic_disc_seg.zip  100%[===================>]  18.41M  58.1MB/s    in 0.3s    

2022-07-09 14:17:30 (58.1 MB/s) - 已保存 “optic_disc_seg.zip” [19300588/19300588])

/opt/conda/envs/python35-paddle120-env/lib/python3.7/site-packages/setuptools/depends.py:2: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  import imp
/home/aistudio/PaddleSeg/paddleseg/models/losses/rmi_loss.py:78: DeprecationWarning: invalid escape sequence \i
  """
2022-07-09 14:17:32 [INFO]	
------------Environment Information-------------
platform: Linux-5.4.0-104-generic-x86_64-with-debian-stretch-sid
Python: 3.7.4 (

## 下载数据集

In [7]:
# 下载 Cityscapes 和 Camvid 数据集
! wget https://paddleseg.bj.bcebos.com/dataset/cityscapes.tar
! wget https://paddleseg.bj.bcebos.com/dataset/camvid.tar

--2022-07-09 14:21:12--  https://paddleseg.bj.bcebos.com/dataset/cityscapes.tar
正在解析主机 paddleseg.bj.bcebos.com (paddleseg.bj.bcebos.com)... 100.67.200.6
正在连接 paddleseg.bj.bcebos.com (paddleseg.bj.bcebos.com)|100.67.200.6|:443... 已连接。
已发出 HTTP 请求，正在等待回应... 200 OK
长度： 12493086720 (12G) [application/x-tar]
正在保存至: “cityscapes.tar”

cityscapes.tar      100%[===================>]  11.63G   112MB/s    in 1m 45s  

2022-07-09 14:22:57 (113 MB/s) - 已保存 “cityscapes.tar” [12493086720/12493086720])

--2022-07-09 14:22:58--  https://paddleseg.bj.bcebos.com/dataset/camvid.tar
正在解析主机 paddleseg.bj.bcebos.com (paddleseg.bj.bcebos.com)... 100.67.200.6
正在连接 paddleseg.bj.bcebos.com (paddleseg.bj.bcebos.com)|100.67.200.6|:443... 已连接。
已发出 HTTP 请求，正在等待回应... 200 OK
长度： 631654400 (602M) [application/x-tar]
正在保存至: “camvid.tar”

camvid.tar          100%[===================>] 602.39M  97.6MB/s    in 6.3s    

2022-07-09 14:23:04 (96.4 MB/s) - 已保存 “camvid.tar” [631654400/631654400])



## 解压数据集

In [8]:
! tar xf camvid.tar -C data/
! tar xf cityscapes.tar -C data/

## 模型训练

In [5]:
%cd ~/PaddleSeg/
!export CUDA_VISIBLE_DEVICES=0 && export model=pp_liteseg_stdc2_cityscapes_1024x512_scale0.75_160k && python -m paddle.distributed.launch train.py \
    --config configs/pp_liteseg/${model}.yml \
    --save_dir output/${model} \
    --save_interval 300 \
    --num_workers 3 \
    --do_eval \
    --use_vdl

/home/aistudio/PaddleSeg
LAUNCH INFO 2022-07-09 14:59:18,170 -----------  Configuration  ----------------------
LAUNCH INFO 2022-07-09 14:59:18,170 devices: None
LAUNCH INFO 2022-07-09 14:59:18,170 elastic_level: -1
LAUNCH INFO 2022-07-09 14:59:18,171 elastic_timeout: 30
LAUNCH INFO 2022-07-09 14:59:18,171 gloo_port: 6767
LAUNCH INFO 2022-07-09 14:59:18,171 host: None
LAUNCH INFO 2022-07-09 14:59:18,171 job_id: default
LAUNCH INFO 2022-07-09 14:59:18,171 legacy: False
LAUNCH INFO 2022-07-09 14:59:18,171 log_dir: log
LAUNCH INFO 2022-07-09 14:59:18,171 log_level: INFO
LAUNCH INFO 2022-07-09 14:59:18,171 master: None
LAUNCH INFO 2022-07-09 14:59:18,171 max_restart: 3
LAUNCH INFO 2022-07-09 14:59:18,171 nnodes: 1
LAUNCH INFO 2022-07-09 14:59:18,171 nproc_per_node: None
LAUNCH INFO 2022-07-09 14:59:18,171 rank: -1
LAUNCH INFO 2022-07-09 14:59:18,171 run_mode: collective
LAUNCH INFO 2022-07-09 14:59:18,171 server_num: None
LAUNCH INFO 2022-07-09 14:59:18,171 servers: 
LAUNCH INFO 2022-07-09

In [1]:
# 如果算力卡时长不足,可以另选时间恢复训练
%cd ~/PaddleSeg/
!export CUDA_VISIBLE_DEVICES=0 && export model=pp_liteseg_stdc2_cityscapes_1024x512_scale0.75_160k && python -m paddle.distributed.launch train.py \
    --config configs/pp_liteseg/${model}.yml \
    --save_dir output/${model} \
    --resume_model output/${model}/iter_50000 \
    --save_interval 1000 \
    --num_workers 3 \
    --do_eval \
    --use_vdl

/home/aistudio/PaddleSeg
LAUNCH INFO 2022-07-10 00:08:03,158 -----------  Configuration  ----------------------
LAUNCH INFO 2022-07-10 00:08:03,158 devices: None
LAUNCH INFO 2022-07-10 00:08:03,158 elastic_level: -1
LAUNCH INFO 2022-07-10 00:08:03,158 elastic_timeout: 30
LAUNCH INFO 2022-07-10 00:08:03,158 gloo_port: 6767
LAUNCH INFO 2022-07-10 00:08:03,158 host: None
LAUNCH INFO 2022-07-10 00:08:03,158 job_id: default
LAUNCH INFO 2022-07-10 00:08:03,158 legacy: False
LAUNCH INFO 2022-07-10 00:08:03,158 log_dir: log
LAUNCH INFO 2022-07-10 00:08:03,158 log_level: INFO
LAUNCH INFO 2022-07-10 00:08:03,158 master: None
LAUNCH INFO 2022-07-10 00:08:03,158 max_restart: 3
LAUNCH INFO 2022-07-10 00:08:03,158 nnodes: 1
LAUNCH INFO 2022-07-10 00:08:03,158 nproc_per_node: None
LAUNCH INFO 2022-07-10 00:08:03,158 rank: -1
LAUNCH INFO 2022-07-10 00:08:03,158 run_mode: collective
LAUNCH INFO 2022-07-10 00:08:03,158 server_num: None
LAUNCH INFO 2022-07-10 00:08:03,158 servers: 
LAUNCH INFO 2022-07-10

## 模型评估


In [3]:
!export CUDA_VISIBLE_DEVICES=0 && export model=pp_liteseg_stdc2_cityscapes_1024x512_scale0.75_160k && python val.py \
    --config configs/pp_liteseg/${model}.yml \
    --model_path output/${model}/best_model/model.pdparams \
    --num_workers 3

2022-07-10 17:59:27 [INFO]	
---------------Config Information---------------
batch_size: 4
iters: 160000
loss:
  coef:
  - 1
  - 1
  - 1
  types:
  - min_kept: 130000
    type: OhemCrossEntropyLoss
  - min_kept: 130000
    type: OhemCrossEntropyLoss
  - min_kept: 130000
    type: OhemCrossEntropyLoss
lr_scheduler:
  end_lr: 0
  learning_rate: 0.005
  power: 0.9
  type: PolynomialDecay
  warmup_iters: 1000
  warmup_start_lr: 1.0e-05
model:
  backbone:
    pretrained: https://bj.bcebos.com/paddleseg/dygraph/PP_STDCNet2.tar.gz
    type: STDC2
  type: PPLiteSeg
optimizer:
  momentum: 0.9
  type: sgd
  weight_decay: 0.0005
test_config:
  aug_eval: true
  scales: 0.75
train_dataset:
  dataset_root: data/cityscapes
  mode: train
  transforms:
  - max_scale_factor: 1.5
    min_scale_factor: 0.125
    scale_step_size: 0.125
    type: ResizeStepScaling
  - crop_size:
    - 1024
    - 512
    type: RandomPaddingCrop
  - type: RandomHorizontalFlip
  - brightness_range: 0.5
    contrast_range: 0.5


mIoU 为 0.7519, 与原始论文的 0.7525 非常接近, 训练圆满完成!

## 模型预测

In [3]:
%cd ~/PaddleSeg/
!python predict.py \
       --config configs/pp_liteseg/pp_liteseg_stdc2_cityscapes_1024x512_scale0.75_160k.yml \
       --model_path output/pp_liteseg_stdc2_cityscapes_1024x512_scale0.75_160k/best_model/model.pdparams \
       --image_path data/cityscapes/leftImg8bit/test/leverkusen/leverkusen_000018_000019_leftImg8bit.png \
       --save_dir ~/work/prediction

/home/aistudio/PaddleSeg
/opt/conda/envs/python35-paddle120-env/lib/python3.7/site-packages/setuptools/depends.py:2: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  import imp
2022-07-20 16:47:27 [INFO]	
---------------Config Information---------------
batch_size: 4
iters: 160000
loss:
  coef:
  - 1
  - 1
  - 1
  types:
  - min_kept: 130000
    type: OhemCrossEntropyLoss
  - min_kept: 130000
    type: OhemCrossEntropyLoss
  - min_kept: 130000
    type: OhemCrossEntropyLoss
lr_scheduler:
  end_lr: 0
  learning_rate: 0.005
  power: 0.9
  type: PolynomialDecay
  warmup_iters: 1000
  warmup_start_lr: 1.0e-05
model:
  backbone:
    pretrained: https://bj.bcebos.com/paddleseg/dygraph/PP_STDCNet2.tar.gz
    type: STDC2
  type: PPLiteSeg
optimizer:
  momentum: 0.9
  type: sgd
  weight_decay: 0.0005
test_config:
  aug_eval: true
  scales: 0.75
train_dataset:
  dataset_root: data/cityscapes
  mode: train
  transforms:

预测的结果：
![](work/prediction/added_prediction/leverkusen_000018_000019_leftImg8bit.png)
![](work/prediction/pseudo_color_prediction/leverkusen_000018_000019_leftImg8bit.png)


## 模型导出

In [5]:
%cd ~/PaddleSeg/
!python export.py \
       --config configs/pp_liteseg/pp_liteseg_stdc2_cityscapes_1024x512_scale0.75_160k.yml \
       --model_path output/pp_liteseg_stdc2_cityscapes_1024x512_scale0.75_160k/best_model/model.pdparams \
       --save_dir ~/work/models \
       --input_shape 1 3 514 1024

/home/aistudio/PaddleSeg
/opt/conda/envs/python35-paddle120-env/lib/python3.7/site-packages/setuptools/depends.py:2: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  import imp
2022-07-20 17:14:02 [INFO]	Loading pretrained model from https://bj.bcebos.com/paddleseg/dygraph/PP_STDCNet2.tar.gz
2022-07-20 17:14:03 [INFO]	There are 265/265 variables loaded into STDCNet.
2022-07-20 17:14:03 [INFO]	Loaded trained params of model successfully.
2022-07-20 17:14:06 [INFO]	Model is saved in /home/aistudio/work/models.


In [1]:
%cd ~/PaddleSeg/
!pip install paddle2onnx onnx onnxruntime 'pycuda>=2019.1.1'

/home/aistudio/PaddleSeg
Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.9/2.9 MB 5.2 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.1/13.1 MB 3.1 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 3.3 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 3.3 MB/s eta 0:00:0000:0100:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.7/15.7 MB 3.4 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.3/70.3 kB 3.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pycuda: filename=pycuda-2022.1-cp37-cp37m-linux_x86_64.whl size=631846 sha256=5440b832865ee80bafe1d0eac314e1db78aa103beaf27ce6c9dd566ee633a03e
  Stored in directory: /home/aistudio/.cache/pip/wh

### 导出 onnx 模型

In [3]:
%cd ~/PaddleSeg/
!paddle2onnx --model_dir ~/work/models \
            --model_filename model.pdmodel \
            --params_filename model.pdiparams \
            --opset_version 11 \
            --save_file ~/work/models/model.onnx

/home/aistudio/PaddleSeg
2022-07-20 19:26:02 [WARNING]	[Deprecated] `paddle2onnx.command.program2onnx` will be deprecated in the future version, the recommended usage is `paddle2onnx.export`
2022-07-20 19:26:06 [INFO]	ONNX model generated is valid.
2022-07-20 19:26:06 [INFO]	ONNX model saved in /home/aistudio/work/models/model.onnx
2022-07-20 19:26:06 [INFO]	===============Make PaddlePaddle Better!================
2022-07-20 19:26:06 [INFO]	A little survey: https://iwenjuan.baidu.com/?code=r8hu2s
